Challenge 1: Demographics and Relationships involves understanding the city’s demographics. Given social networks and other information about the city, you will analyze the available data to prepare a one-page fact sheet about the city’s demographics, its neighborhoods, and its business base.

In Challenge 1, you will use visual analytic techniques to address the following questions:


- Consider the social activities in the community. What patterns do you see in the social networks in the town? Describe up to ten significant patterns you observe, with evidence and rationale. Limit your response to 10 images and 500 words.
- Identify the predominant business base of the town, and describe patterns you observe. Limit your response to 10 images and 500 words.
- From your answers to questions 1-3, assemble a one-page summary that provides the key information to share with residents about the town.

- Assuming the volunteers are representative of the city’s population, characterize what you can about the demographics of the town. Provide your rationale and supporting data. Limit your response to 10 images and 500 words.

In [1]:
base_path = '/home/hmreumann/Documents/2022-ECD/datavis/vast/'
# base_path = 'C:/....'

In [2]:
import duckdb
import altair as alt
import pandas as pd

In [3]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [4]:
con = duckdb.connect(database=':memory:')

In [5]:
activity_logs_path = base_path + 'parquet_activity_logs/ParticipantStatusLogs*.parquet'

In [6]:
# fields of activity logs table

con.execute(F"SUMMARIZE SELECT * FROM read_parquet('{activity_logs_path}');").df()

column_name column_type                   min  \
0           timestamp     VARCHAR  2022-03-01T00:00:00Z   
1     currentLocation     VARCHAR                 POINT   
2       participantId      BIGINT                     0   
3         currentMode     VARCHAR                AtHome   
4        hungerStatus     VARCHAR            BecameFull   
5         sleepStatus     VARCHAR                 Awake   
6         apartmentId      BIGINT                     1   
7    availableBalance      DOUBLE    -681.6505879983722   
8               jobId      BIGINT                     1   
9     financialStatus     VARCHAR                Stable   
10    dailyFoodBudget      BIGINT                    12   
11  weeklyExtraBudget      DOUBLE   -14.491930381363964   

                                             max approx_unique  \
0                           2023-05-24T04:30:00Z        126773   
1   POINT (999.8961575371305 1439.1007707482759)         26242   
2                                           1010          1021   
3                                      Transport             5   
4                                       Starving             6   
5                                       Sleeping             3   
6                                           1733           868   
7                             240048.69855951148       1818104   
8                                           1326          1193   
9                                       Unstable             3   
10                                            20             3   
11                             99253.87074954412        728420   

                   avg                 std                q25  \
0                  NaN                 NaN                NaN   
1                  NaN                 NaN                NaN   
2   481.29721917296007    294.283984223849                225   
3                  NaN                 NaN                NaN   
4                  NaN                 NaN                NaN   
5                  NaN                 NaN                NaN   
6     850.846232233079   514.0393258368995                366   
7   21277.078917946208  23366.914955613738  5899.746198994657   
8    675.0105813421686  388.60850882910626                332   
9                  NaN                 NaN                NaN   
10  15.594620692424115  3.2336895183497214                 12   
11   6129.267803031344   7618.550379729593  1596.299164730355   

                   q50                 q75      count null_percentage  
0                  NaN                 NaN  113923735            0.0%  
1                  NaN                 NaN  113923735            0.0%  
2                  463                 725  113923735            0.0%  
3                  NaN                 NaN  113923735            0.0%  
4                  NaN                 NaN  113923735            0.0%  
5                  NaN                 NaN  113923735            0.0%  
6                  886                1243  113923735           0.14%  
7   13575.690589440723  28321.593350530682  113923735            0.0%  
8                  678                1016  113923735            0.0%  
9                  NaN                 NaN  113923735            0.0%  
10                  16                  20  113923735            0.0%  
11  3512.4838350030527  7535.9634103940125  113923735            0.0%

In [7]:
# Count of participants
events_by_participant = con.execute(f"SELECT participantId, COUNT(*) as count_of_events FROM read_parquet('{activity_logs_path}') GROUP BY participantId HAVING count_of_events > 40000;").df()

alt.Chart(events_by_participant).mark_bar().encode(
    alt.X("count_of_events:Q", bin=True),
    y='count()',
)

alt.Chart(...)

In [8]:
# Distinct currentMode
con.execute(f"SELECT DISTINCT currentMode FROM read_parquet('{activity_logs_path}');").df()

currentMode
0     Transport
1  AtRecreation
2        AtHome
3        AtWork
4  AtRestaurant
5           NaN

In [9]:
# Distinct financial status
con.execute(f"SELECT DISTINCT financialStatus FROM read_parquet('{activity_logs_path}');").df()

financialStatus
0          Stable
1             NaN
2        Unstable
3         Unknown

In [10]:
# Transportation
transportation_data = con.execute(f"SELECT currentLocation FROM read_parquet('{activity_logs_path}') WHERE currentMode = 'Transport';").df()

In [11]:
# Participants
participants_path = base_path + 'attributes/Participants.parquet'


In [12]:
con.execute(f"SUMMARIZE SELECT * FROM read_parquet('{participants_path}');").df()

column_name column_type        min          max approx_unique  \
0   participantId     INTEGER          0         1010          1021   
1   householdSize     INTEGER          1            3             3   
2        haveKids     BOOLEAN      false         true             2   
3             age     INTEGER         18           60            43   
4  educationLevel     VARCHAR  Bachelors          Low             4   
5   interestGroup     VARCHAR          A            J            10   
6       joviality      DOUBLE   0.000204  0.999233967          1018   

                   avg                 std                  q25  \
0                505.0   291.9948629685118                  252   
1   1.9643916913946589  0.7939861215899384                    1   
2                  NaN                 NaN                  NaN   
3   39.074183976261125  12.379295882093464                   29   
4                  NaN                 NaN                  NaN   
5                  NaN                 NaN                  NaN   
6  0.49379372796933807  0.2913509988561309  0.23887533580769232   

                  q50                 q75  count null_percentage  
0                 505                 758   1011            0.0%  
1                   2                   3   1011            0.0%  
2                 NaN                 NaN   1011            0.0%  
3                  39                  50   1011            0.0%  
4                 NaN                 NaN   1011            0.0%  
5                 NaN                 NaN   1011            0.0%  
6  0.4767412182444444  0.7463038686859504   1011            0.0%

In [13]:
# Edad de los participantes Vs educationLevel
source = con.execute(f"SELECT age, educationLevel FROM read_parquet('{participants_path}') GROUP BY age, educationLevel;").df()

alt.Chart(source).mark_circle().encode(
    x = alt.X('age', bin=True),
    y = alt.Y('educationLevel:O', sort=['Graduate','Bachelors','HighSchoolOrCollege','Low']),
    size='count()'
)

alt.Chart(...)

In [14]:
# Zonas residenciales

source = con.execute(f"SELECT currentLocation FROM read_parquet('{activity_logs_path}') WHERE currentMode = 'AtHome' GROUP BY participantId, currentLocation;").df()


In [15]:
# Extraemos Coordenadas x e y cada posición

def extraer_coordenadas(source):
    source2 = source['currentLocation'].str.split(' ', 1, expand=True)
    source3 = source2[1].str.split(' ', 1, expand=True)

    x = source3[0].str.split('(', 1, expand=True)
    y = source3[1].str.split(')', 1, expand=True)

    data = [x[1], y[0]]

    df1 = pd.DataFrame(x[1])
    df2 = pd.DataFrame(y[0])
    newDf = df1.join(df2)
    return newDf.rename(columns={1: 'longitud', 0: 'latitud'})

In [16]:
coordenadas_homes = extraer_coordenadas(source)

In [17]:
residential = alt.Chart(coordenadas_homes).mark_rect().encode(
    alt.X('longitud:Q', scale=alt.Scale(domain=(-5000, 2800)), bin=alt.Bin(maxbins=50)),
    alt.Y('latitud:Q', scale=alt.Scale(domain=(0, 8000)), bin=alt.Bin(maxbins=50)),
    alt.Color('count():Q', scale=alt.Scale(scheme='goldred'))
).properties(
    title='Homes'
)

In [18]:
# Zonas Laborales

work_data = con.execute(f"""
    SELECT currentLocation 
    FROM read_parquet('{activity_logs_path}') 
    WHERE currentMode = 'AtWork' 
    GROUP BY participantId, currentLocation;
""").df()

In [19]:
coordenadas_work = extraer_coordenadas(work_data)

In [20]:
work = alt.Chart(coordenadas_work).mark_rect().encode(
    alt.X('longitud:Q', scale=alt.Scale(domain=(-5000, 2800)), bin=alt.Bin(maxbins=50)),
    alt.Y('latitud:Q', scale=alt.Scale(domain=(0, 8000)), bin=alt.Bin(maxbins=50)),
    alt.Color('count():Q', scale=alt.Scale(scheme='goldred'))
).properties(
    title='Work Places'
)

In [21]:
# Zonas Restaurant

restaurant_data = con.execute(f"""
    SELECT currentLocation 
    FROM read_parquet('{activity_logs_path}') 
    WHERE currentMode = 'AtRestaurant' 
    GROUP BY participantId, currentLocation;
""").df()

In [22]:
coordenadas_restaurant = extraer_coordenadas(restaurant_data)

In [23]:
# Zonas Recreation

recreation_data = con.execute(f"""
    SELECT currentLocation 
    FROM read_parquet('{activity_logs_path}') 
    WHERE currentMode = 'AtRecreation' 
    GROUP BY participantId, currentLocation;
""").df()

In [24]:
coordenadas_recreation = extraer_coordenadas(recreation_data)

In [43]:
alt.hconcat(residential, work)

alt.HConcatChart(...)

In [26]:
alt.Chart(coordenadas_restaurant).mark_rect().encode(
    alt.X('longitud:Q', scale=alt.Scale(domain=(-5000, 2800)), bin=alt.Bin(maxbins=50)),
    alt.Y('latitud:Q', scale=alt.Scale(domain=(0, 8000)), bin=alt.Bin(maxbins=50)),
    alt.Color('count():Q', scale=alt.Scale(scheme='purplebluegreen'))
).properties(
    title='Restaurants'
)

alt.Chart(...)

In [27]:
alt.Chart(coordenadas_recreation).mark_rect().encode(
    alt.X('longitud:Q', scale=alt.Scale(domain=(-5000, 2800)), bin=alt.Bin(maxbins=50)),
    alt.Y('latitud:Q', scale=alt.Scale(domain=(0, 8000)), bin=alt.Bin(maxbins=50)),
    alt.Color('count():Q', scale=alt.Scale(scheme='darkgreen'))
).properties(
    title='Recreation'
)

alt.Chart(...)

In [28]:
# Zonas Laborales

transport_positions = con.execute(f"""
    SELECT currentLocation 
    FROM read_parquet('{activity_logs_path}') 
    WHERE currentMode = 'Transport';
""").df()

In [29]:
coordenadas_transport = extraer_coordenadas(work_data)

In [30]:
con.execute(f"""
    SELECT currentMode, count(*)
    FROM read_parquet('{activity_logs_path}') 
    GROUP BY currentMode;
""").df()

currentMode  count_star()
0        AtHome      69236289
1  AtRecreation       5436347
2     Transport      10246066
3  AtRestaurant       1765430
4        AtWork      27239602
5           NaN             1

In [31]:
# transport_data = con.execute(f"""
#     SELECT currentLocation
#     FROM read_parquet('{activity_logs_path}')
#     WHERE currentMode = 'Transport';
# """).df()

In [32]:
# coordenadas_transport = extraer_coordenadas(transport_data)

In [33]:
# coordenadas_transport.count()

In [34]:
# alt.Chart(coordenadas_transport).mark_rect().encode(
#     alt.X('longitud:Q', bin=alt.Bin(maxbins=100)),
#     alt.Y('latitud:Q', bin=alt.Bin(maxbins=100)),
#     alt.Color('count():Q', scale=alt.Scale(scheme='goldred'))
# ).properties(
#     title='Transport'
# )

In [35]:
coordenadas_homes_2 = coordenadas_homes.rename(columns={'longitud': 'longitud_h', 'latitud': 'latitud_h'})

In [36]:

distancias = coordenadas_homes_2.join(coordenadas_work)

In [37]:
distancias['longitud_h'] = distancias['longitud_h'].astype(float)
distancias['latitud_h'] = distancias['latitud_h'].astype(float)
distancias['longitud'] = distancias['longitud'].astype(float)
distancias['latitud'] = distancias['latitud'].astype(float)

In [38]:
distancias['manhattan'] = abs(distancias.longitud_h - distancias.longitud) + abs(distancias.latitud_h - distancias.latitud)

In [39]:
base = alt.Chart(distancias)

bar = base.mark_bar().encode(
    x=alt.X('manhattan:Q', bin=True),
    y='count()'
)

rule = base.mark_rule(color='red').encode(
    x='mean(manhattan):Q',
    size=alt.value(5)
)

bar + rule

alt.LayerChart(...)

In [40]:
# Transport
transport_data = con.execute(f"""
    SELECT currentLocation 
    FROM read_parquet('{activity_logs_path}') 
    WHERE currentMode = 'Transport';
""").df().sample(n=50000)

In [41]:
coordenadas_transport = extraer_coordenadas(transport_data)

In [44]:
alt.Chart(coordenadas_transport).mark_rect().encode(
    alt.X('longitud:Q', scale=alt.Scale(domain=(-5000, 2800)), bin=alt.Bin(maxbins=200)),
    alt.Y('latitud:Q', scale=alt.Scale(domain=(0, 8000)), bin=alt.Bin(maxbins=200)),
    alt.Color('count():Q', scale=alt.Scale(scheme='reds'))
).properties(
    title='Transport'
)

alt.Chart(...)